# Canasta estatal, Analisis de datos

20/06/2025
Este notebook contiene el analisis de datos basico en el que se basa el dashboard. Por fines practicos se realiza solo para el año 2023

## Paquetes

In [2]:

import pandas as pd
import os
from pathlib import Path
import plotly.express as px
import numpy as np
import plotly.figure_factory as ff
from scipy.stats import gaussian_kde
import plotly.graph_objects as go
from scipy.stats import gmean  # Para la media geométrica
import plotly.graph_objects as go
from unidecode import unidecode
import geopandas as gpd
from shapely.geometry import Point
import re

## Functions to Read data

In [3]:
def load_data(year):
    current_folder = Path(os.getcwd())
    filename = f"{year}_match_variedades_canasta_Estatal.xlsx"
    folder_name = Path("source_data")
    full_path = current_folder / folder_name / filename
    
    if not (current_folder / folder_name).exists():
        raise FileNotFoundError(f"No se encontró la carpeta {folder_name}")
    if not full_path.exists():
        raise FileNotFoundError(f"No se encontró el archivo {filename} en {folder_name}")
    
    return pd.read_excel(full_path, sheet_name=0)

def get_variedades(dataframe, codigo_col='CÓDIGO DE INSUMO', presentacion_col='PRESENTACION'):
    """
    Funcion que devuelve un dataframe con el codigo de insumo
    y las variedades como una lista
    se accede al dataframe por medio del codigo de insumo,
    get_variedades()[Codigo_Insumo] donde Codigo_Insumo es un 
    numero o un valor alfnumerico
    Args:
        dataframe (_dataframe_): dataframe que contiene el codigo de insumo
                                 y las presentaciones de cada insumo
        codigo_col (_str_):     nombre la columna con el codigo de insumo
        presentacion_col (_str_): nombre de la columna con las diferentes presentaciones
    """
    return dataframe.groupby(codigo_col)[presentacion_col].unique()

In [4]:
dtYear=load_data(2023)
dtYear.columns

Index(['Codigo Insumo', 'Unidad Original', 'Unidad Match', 'Score v',
       'Match Valido', 'Razon Rechazo', 'Cantidad Extraida',
       'Unidad Normalizada', 'json ID', 'Filename', 'NOG', 'Descripcion',
       'NIT Oferente', 'Oferente', 'Grupo', 'Subgrupo', 'Renglon',
       'Insumo Match', 'Producto', 'Unidad de Medida', 'Marca',
       'Cantidad Ofertada', 'Precio unitario', 'Monto ofertado',
       'Caracteristicas', 'Modalidad', 'Adjudicado', 'Fecha Publicacion',
       'Hora Publicacion', 'Fecha Adjudicacion', 'Hora Adjudicacion',
       'NIT Comprador', 'Comprador', 'Score', 'texto_busqueda'],
      dtype='object')

In [5]:
dtYear

Codigo Insumo              Unidad Original Unidad Match   Score v  \
0              1821  Botella - 445 Mililitro(ml)          NaN  0.000000   
1              1821  Botella - 445 Mililitro(ml)          NaN  0.000000   
2              1821  Botella - 445 Mililitro(ml)          NaN  0.000000   
3              1821  Botella - 445 Mililitro(ml)          NaN  0.000000   
4              1821  Botella - 445 Mililitro(ml)          NaN  0.000000   
...             ...                          ...          ...       ...   
6500         105780            Unidad - 1 Unidad  UNIDAD 1 ()  0.935684   
6501         105780            Unidad - 1 Unidad  UNIDAD 1 ()  0.935684   
6502         105780            Unidad - 1 Unidad  UNIDAD 1 ()  0.935684   
6503         105780            Unidad - 1 Unidad  UNIDAD 1 ()  0.935684   
6504         105780            Unidad - 1 Unidad  UNIDAD 1 ()  0.935684   

      Match Valido                  Razon Rechazo  Cantidad Extraida  \
0            False  Diferencia en cantidad/unidad              445.0   
1            False  Diferencia en cantidad/unidad              445.0   
2            False  Diferencia en cantidad/unidad              445.0   
3            False  Diferencia en cantidad/unidad              445.0   
4            False  Diferencia en cantidad/unidad              445.0   
...            ...                            ...                ...   
6500          True                            NaN                1.0   
6501          True                            NaN                1.0   
6502          True                            NaN                1.0   
6503          True                            NaN                1.0   
6504          True                            NaN                1.0   

     Unidad Normalizada  json ID                             Filename  ...  \
0             mililitro     2860  19058594_2023_01_webpage_source.txt  ...   
1             mililitro    11361  19065930_2023_01_webpage_source.txt  ...   
2             mililitro    20185  19066503_2023_01_webpage_source.txt  ...   
3             mililitro    11913  19066805_2023_01_webpage_source.txt  ...   
4             mililitro     3223  19067119_2023_01_webpage_source.txt  ...   
...                 ...      ...                                  ...  ...   
6500             unidad    21460  20726279_2023_10_webpage_source.txt  ...   
6501             unidad    20816  20932774_2023_10_webpage_source.txt  ...   
6502             unidad       56  21094373_2023_10_webpage_source.txt  ...   
6503             unidad    17432  21263205_2023_11_webpage_source.txt  ...   
6504             unidad     8203  21636818_2023_12_webpage_source.txt  ...   

                                              Modalidad Adjudicado  \
0     Compra Directa con Oferta Electrónica (Art. 43...          1   
1     Compra Directa con Oferta Electrónica (Art. 43...          1   
2     Compra Directa con Oferta Electrónica (Art. 43...          1   
3     Compra Directa con Oferta Electrónica (Art. 43...          1   
4     Compra Directa con Oferta Electrónica (Art. 43...          1   
...                                                 ...        ...   
6500                           Cotización (Art. 38 LCE)          1   
6501                           Cotización (Art. 38 LCE)          1   
6502                           Cotización (Art. 38 LCE)          1   
6503                   Licitación Pública (Art. 17 LCE)          1   
6504                           Cotización (Art. 38 LCE)          1   

     Fecha Publicacion Hora Publicacion  Fecha Adjudicacion  \
0           2023-01-19         14:17:52          2023-01-24   
1           2023-01-19         14:21:08          2023-01-24   
2           2023-01-19         14:27:14          2023-01-24   
3           2023-01-19         14:31:24          2023-01-24   
4           2023-01-19         15:06:04          2023-01-24   
...                ...              ...                 ...   
6500        2023-10-0

## Functions to Analize data

In [6]:
def get_variedades(dataframe, codigo_col='CÓDIGO DE INSUMO', presentacion_col='PRESENTACION'):
    """
    Funcion que devuelve un dataframe con el codigo de insumo
    y las variedades como una lista
    se accede al dataframe por medio del codigo de insumo,
    get_variedades()[Codigo_Insumo] donde Codigo_Insumo es un 
    numero o un valor alfnumerico
    Args:
        dataframe (_dataframe_): dataframe que contiene el codigo de insumo
                                 y las presentaciones de cada insumo
        codigo_col (_str_):     nombre la columna con el codigo de insumo
        presentacion_col (_str_): nombre de la columna con las diferentes presentaciones
    """
    return dataframe.groupby(codigo_col)[presentacion_col].unique()

In [7]:
def get_dfCode_variedad(dataframe,InsumoCode,variedad,codigo_col='Codigo Insumo',variedad_col="Unidad de Medida"):
    """
    "Funcion que devuelve un dataframe con el la data filtrada
    siguiendo el codigo de insumo y la variedad seleccionada
    """
    df=dataframe[dataframe[codigo_col]==InsumoCode].copy()
    return df[df[variedad_col]==variedad]

In [8]:
def get_DataPlot_variety(dataframe,InsumoCode,variedad, codigo_col='Codigo Insumo', variedad_col='Unidad de Medida',  UnitsSold_col='Cantidad Ofertada', UnitPrice_col='Precio unitario'):
    """_summary_:  Devuelve una lista con los precios unitarios repetidos n-veces
                   donde n es el numero de unidades vendidas

    Args:
        dataframe (_type_): Es un dataframe de pandas
        InsumoCode (_type_): codigo de insumo
        variedad (_type_): nombre de la variedad
        codigo_col (_type_): nombre de la columna con el codigo de insumo
        variedad_col (_type_): nombre de la columna con las variedades
        UnitsSold_col (_type_): nombre de la columna con las unidades vendidas
        UnitPrice_col (_type_): nombre de la columna con el precio por unidad
    """
    df=get_dfCode_variedad(dataframe,InsumoCode,variedad,codigo_col,variedad_col)
    dataPlot = []
    for precio, cantidad in zip(df[UnitsSold_col], df[UnitPrice_col]):
        dataPlot.extend([precio] * round(float(cantidad)))
    return dataPlot
    

In [9]:
variety_dtYear=get_variedades(dtYear,'Codigo Insumo','Unidad de Medida')
variety_dtYear

Codigo Insumo
11                                      [Unidad - 1 Unidad]
37                                      [Unidad - 1 Unidad]
69        [Unidad, Envase - 460 Mililitro(ml), Envase - ...
70        [Envase - 1 Galón(gal), Unidad, Envase - 500 M...
72        [Envase - 1 Galón(gal), Envase - 500 Mililitro...
                                ...                        
144838                                  [Unidad - 1 Unidad]
144839                                  [Unidad - 1 Unidad]
144840                                  [Unidad - 1 Unidad]
144841                                  [Unidad - 1 Unidad]
144843                                  [Unidad - 1 Unidad]
Name: Unidad de Medida, Length: 274, dtype: object

In [10]:
dfVariety=get_dfCode_variedad(dtYear,1821,variety_dtYear[1821][0],'Codigo Insumo','Unidad de Medida')
dfVariety[["Codigo Insumo", 'Unidad de Medida', 'Cantidad Ofertada', 'Precio unitario']]

Codigo Insumo             Unidad de Medida  Cantidad Ofertada  \
0             1821  Botella - 445 Mililitro(ml)                600   
1             1821  Botella - 445 Mililitro(ml)                600   
2             1821  Botella - 445 Mililitro(ml)                558   
3             1821  Botella - 445 Mililitro(ml)                440   
4             1821  Botella - 445 Mililitro(ml)                600   
..             ...                          ...                ...   
116           1821  Botella - 445 Mililitro(ml)                486   
117           1821  Botella - 445 Mililitro(ml)                584   
118           1821  Botella - 445 Mililitro(ml)                307   
120           1821  Botella - 445 Mililitro(ml)               1797   
121           1821  Botella - 445 Mililitro(ml)                789   

     Precio unitario  
0              11.25  
1              11.25  
2              11.50  
3              11.50  
4              11.25  
..               ...  
116            11.00  
117            10.80  
118            10.85  
120            10.69  
121            11.00  

[111 rows x 4 columns]

In [11]:
dtYear.columns

Index(['Codigo Insumo', 'Unidad Original', 'Unidad Match', 'Score v',
       'Match Valido', 'Razon Rechazo', 'Cantidad Extraida',
       'Unidad Normalizada', 'json ID', 'Filename', 'NOG', 'Descripcion',
       'NIT Oferente', 'Oferente', 'Grupo', 'Subgrupo', 'Renglon',
       'Insumo Match', 'Producto', 'Unidad de Medida', 'Marca',
       'Cantidad Ofertada', 'Precio unitario', 'Monto ofertado',
       'Caracteristicas', 'Modalidad', 'Adjudicado', 'Fecha Publicacion',
       'Hora Publicacion', 'Fecha Adjudicacion', 'Hora Adjudicacion',
       'NIT Comprador', 'Comprador', 'Score', 'texto_busqueda'],
      dtype='object')

In [12]:
variety_dtYear[1821]

array(['Botella - 445 Mililitro(ml)', 'Bote - 1 Galón(gal)',
       'Envase - 3750 Mililitro(ml)', 'Envase - 3200 Mililitro(ml)',
       'Botella - 800 Mililitro(ml)', 'Botella - 175 Mililitro(ml)'],
      dtype=object)

In [13]:
insumoCode=1821
dtPlotVariety=get_DataPlot_variety(dtYear,insumoCode,variety_dtYear[insumoCode][0])
dtPlotVariety

[600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 558,
 558,
 558,
 558,
 558,
 558,
 558,
 558,
 558,
 558,
 558,
 558,
 440,
 440,
 440,
 440,
 440,
 440,
 440,
 440,
 440,
 440,
 440,
 440,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 281,
 281,
 281,
 281,
 281,
 281,
 281,
 281,
 281,
 281,
 281,
 281,
 843,
 843,
 843,
 843,
 843,
 843,
 843,
 843,
 843,
 843,
 843,
 843,
 701,
 701,
 701,
 701,
 701,
 701,
 701,
 701,
 701,
 701,
 701,
 701,
 390,
 390,
 390,
 390,
 390,
 390,
 390,
 390,
 390,
 390,
 390,
 217,
 217,
 217,
 217,
 217,
 217,
 217,
 217,
 217,
 217,
 217,
 217,
 263,
 263,
 263,
 263,
 263,
 263,
 263,
 263,
 263,
 263,
 263,
 263,
 263,
 282,
 282,
 282,
 282,
 282,
 282,
 282,
 282,
 282,
 282,
 282,
 282,
 686,
 686,
 686,
 686,
 686,
 686,
 686,
 686,
 686,
 686,
 686,
 686,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600,
 600

## Plots

In [14]:
INEBlueColors=[px.colors.qualitative.G10[0], px.colors.qualitative.D3[0], px.colors.qualitative.G10[0],
               px.colors.qualitative.T10[0], px.colors.qualitative.T10[0], px.colors.qualitative.Set3[4]  ]
INEGreenColors=[px.colors.qualitative.Vivid[5]]
INEOrangeColors=[px.colors.qualitative.D3[1]]
INEBlueColors

['#3366CC', '#1F77B4', '#3366CC', '#4C78A8', '#4C78A8', 'rgb(128,177,211)']

### Histograma por variedad

In [15]:
insumoCode = 1821
variedad = variety_dtYear[insumoCode][0] #variedad
dfVariety = get_dfCode_variedad(dtYear, 1821, variedad, 'Codigo Insumo', 'Unidad de Medida') #dataframe por variedad

def plot_Hvariety(dtYear,InsumoCode,variedad, CL=95, insumo_col='Codigo Insumo',variedad_col='Unidad de Medida'):
    """Genera histograma por codigo de insumo y varidad de un año especifico usando plotly
    Args:
        CL : Confidence level, default 95%
        dtYear (_type_): _description_
        InsumoCode (_type_): _description_
        variedad (_type_): _description_
        insumo_col (_type_): _description_
        vierdad_col (_type_): _description_
    """
    dfVariety = get_dfCode_variedad(dtYear, InsumoCode, variedad, insumo_col, variedad_col) #dataframe por variedad
# Número de bins usando la regla de Sturges (ajustado para suma)
    Nbins = int(1 + np.log2(dfVariety['Cantidad Ofertada'].sum()))
    #print("Número de bins:", Nbins)

    media_precio = dfVariety["Precio unitario"].mean()
    data = dfVariety["Precio unitario"].dropna()
    gmean_val = gmean(data)  # Media geométrica

    # Calcular KDE
    kde = gaussian_kde(data)
    x_kde = np.linspace(data.min(), data.max(), 500)
    y_kde = kde(x_kde)

    # Escalar el KDE para suma de cantidades
    sum_total = dfVariety["Cantidad Ofertada"].sum()
    range_x = data.max() - data.min()
    y_kde_scaled = y_kde * sum_total * (range_x / Nbins)

    # Calcular cuartiles
    CLevel=CL #Confidence Level
    QLow=50-(CLevel/2)
    QHig=(CLevel/2)+50
    q_low = np.percentile(data, QLow)
    q_high = np.percentile(data, QHig)

    # Crear histograma (suma de cantidades)
    fig = px.histogram(
        dfVariety,
        x="Precio unitario",
        y="Cantidad Ofertada",
        color_discrete_sequence=[INEBlueColors[3]],
        histfunc='sum',
        nbins=Nbins
    )

    # Añadir KDE escalado
    fig.add_trace(
        go.Scatter(
            x=x_kde,
            y=y_kde_scaled,
            mode='lines',
            line=dict(color='red', width=2),
            hovertemplate='Precio: %{x:.2f}<br>KDE: %{y:.2f}<extra></extra>',
            showlegend=False  # Esto oculta la leyenda "trace 1"
            #name='KDE (Suma Ajustada)'
        )
    )

    # Resaltar cuartiles (opcional)
    fig.add_vrect(
        x0=q_low, x1=q_high,
        fillcolor="lightgray", opacity=0.2,
        annotation_text=f"{CLevel}% de los datos", annotation_position="top left"
    )

    # Línea de media
    fig.add_vline(
        x=media_precio,
        line_dash="dash",
        line_color=INEOrangeColors[0]
        #annotation_text=f"Media: {media_precio:.2f} Q"
    )

    # Ajustes finales
    fig.update_layout(
        xaxis_title=f"Precio Unitario de {variedad} [Q]",
        yaxis_title="Total unidades ofertadas",
        bargap=0.01,
        showlegend=True
    )
    return fig.show()




print("Numero de precios unitarios distintos=", len(data.unique()))
print(f"Media={media_precio:.2f}")
print(f"Media Geometrica={gmean_val:.2f}")
print(f"Precios con un CL de {CLevel:.2f} %")
print(f"Precio maximo={q_low:.3f}")
print(f"Precio minimo={q_high:.3f}")

NameError: name 'data' is not defined

In [29]:
current_folder = Path(os.getcwd())
soruce_folder="source_data"
filename_csv = "2023_all_results_all-MiniLM-L6-v2-similarity-es_score_value_0.7.csv"
dfY=pd.read_csv(current_folder/ soruce_folder / filename_csv, sep=',',
                encoding='utf-8-sig',
                quoting=1, low_memory=False)
variety_dtYear=get_variedades(dfY,'Codigo Insumo','Unidad de Medida')

insumoCode = 1821
CLevel=95
Nvar=2
variedad = variety_dtYear[insumoCode][Nvar] #variedad
plot_Hvariety(dtYear,insumoCode,variedad,CLevel)

### Numero de vendedores por variedad

### Mapa con la ubicacion de los vendedores (por municipio)

In [17]:


# 1. Cargar las ciudades
current_folder = Path(os.getcwd())
soruce_folder="source_data"
filename_citys = "worldcities.csv"
filename_GeoJSON= "gadm41_GTM_2.json"

df = pd.read_csv(current_folder/soruce_folder/filename_citys)
df_gt = df[df['country'] == 'Guatemala'].copy()

# Crear geometría (puntos) a partir de lat/lng
geometry = [Point(xy) for xy in zip(df_gt['lng'], df_gt['lat'])]
gdf_cities = gpd.GeoDataFrame(df_gt, geometry=geometry, crs="EPSG:4326")

# 2. Cargar el GeoJSON (municipios)
gdf_munis = gpd.read_file(current_folder / soruce_folder /filename_GeoJSON)

# 3. Hacer spatial join: asignar municipio a cada ciudad
gdf_joined = gpd.sjoin(gdf_cities, gdf_munis, how="left", predicate="within")

# 4. Agrupar por municipio y sumar población
df_grouped = gdf_joined.groupby("NAME_2").agg({"population": "sum"}).reset_index()
df_grouped.rename(columns={"NAME_2": "municipio"}, inplace=True)

# 5. Crear el choropleth con Plotly
# Añadir columna de población al GeoDataFrame original
gdf_munis = gdf_munis.merge(df_grouped, left_on="NAME_2", right_on="municipio", how="left")

# Llenar NaN en población con 0
gdf_munis["population"] = gdf_munis["population"].fillna(0)

# Usar Plotly para graficar
fig = px.choropleth(
    gdf_munis,
    geojson=gdf_munis.geometry,
    locations=gdf_munis.index,
    color="population",
    hover_name="municipio",
    color_continuous_scale="Blues",
    title="Población por municipio en Guatemala (estimada desde worldcities.csv)"
)

fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":0,"t":50,"l":0,"b":0})
fig.show()


In [18]:
def extraer_zona(direccion):
    """
    Extrae la zona desde una dirección textual.
    Soporta formatos como: z1, z.1, zona 1, z-1, z. 1, etc.
    """
    if not isinstance(direccion, str):
        return None

    direccion = direccion.lower()
    direccion = unidecode(direccion)

    # Regex: busca z, z., z-, zona seguido por espacios opcionales y un número de 1 o 2 dígitos
    match = re.search(r'\b(?:zona|z|z\.|z-)[\s\.]*([0-9]{1,2})\b', direccion)
    if match:
        return f"zona{int(match.group(1))}"
    return None

In [19]:
def plot_map_municipios(dtYear, dfGeoDATA, InsumoCode, variedad, Insumo_col='Codigo Insumo', variety_col='Unidad de Medida'):
    df_ventas = get_dfCode_variedad(dtYear, InsumoCode, variedad, Insumo_col, variety_col)

    # Normalizar clave de municipio en GeoJSON: eliminar TODOS los espacios, minúsculas y quitar acentos
    dfGeoDATA['muni_key'] = dfGeoDATA['NAME_2'].str.replace(' ', '').str.lower().apply(unidecode)  # Corregido: .str.replace
    
    # Normalizar municipios en ventas: eliminar TODOS los espacios, minúsculas y quitar acentos
    df_ventas['muni_key'] = df_ventas['Localidad Oferente'].str.replace(' ', '').str.lower().apply(unidecode)  # Corregido: .str.replace

    # Detectar casos especiales: "guatemala" o "ciudad de guatemala" (ya normalizados sin espacios)
    mask_guatemala = df_ventas['muni_key'].isin(['guatemala', 'ciudaddeguatemala'])  # Corregido: sin espacios
    df_ventas.loc[mask_guatemala, 'zona'] = df_ventas.loc[mask_guatemala, 'Direccion Oferente'].apply(extraer_zona)
    
    # Si se extrajo zona, normalizarla (eliminar espacios, minúsculas, sin acentos) y actualizar muni_key
    mask_zona_valida = mask_guatemala & df_ventas['zona'].notnull()
    df_ventas.loc[mask_zona_valida, 'muni_key'] = (
        df_ventas.loc[mask_zona_valida, 'zona']
        .str.replace(' ', '').str.lower().apply(unidecode)  # Asegurar normalización de la zona
    )
    
    # Agrupar ventas por municipio (clave: muni_key)
    ventas_muni = df_ventas.groupby('muni_key')['Monto ofertado'].sum().reset_index()
    
    # Merge con GeoJSON
    gdf_merge = dfGeoDATA.merge(ventas_muni, on='muni_key', how='left')
    gdf_merge['monto_ofertado'] = gdf_merge['Monto ofertado'].fillna(0)

    # Plot
    fig = px.choropleth(
        gdf_merge,
        geojson=gdf_merge.geometry,
        locations=gdf_merge.index,
        color='monto_ofertado',
        hover_name="NAME_2",
        color_continuous_scale="Blues",
        title=f"Compras totales por municipio\n{variedad}"
    )
    fig.update_geos(fitbounds="locations", visible=False)
    fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})

    
    return fig.show()


In [20]:
#PATHS
current_folder = Path(os.getcwd())
soruce_folder="source_data"
filename_csv = "2023_01_results_matching_all-MiniLM-L6-v2-similarity-es_score_value_0.7.csv"
filename_csv1= "2023_02_results_matching_all-MiniLM-L6-v2-similarity-es_score_value_0.7.csv"
filename_csv2= "2023_03_results_matching_all-MiniLM-L6-v2-similarity-es_score_value_0.7.csv"
filename_GeoJSON= "gadm41_GTM_2.json"

# Cargar la data por municipalidad
gdf_munis1 = gpd.read_file(current_folder/soruce_folder/filename_GeoJSON)
df0=pd.read_csv(current_folder/soruce_folder/filename_csv)
df1=pd.read_csv(current_folder/soruce_folder/filename_csv1)
df2=pd.read_csv(current_folder/soruce_folder/filename_csv2)
dfY=pd.concat([df0,df1,df2],axis=0, ignore_index=True)
#codigo de insumo y varidad
insumoCode = 1821
Nvar=0
variety_dtYear=get_variedades(dfY,'Codigo Insumo','Unidad de Medida')
variedad = variety_dtYear[insumoCode][Nvar] #variedad

plot_map_municipios(dfY,gdf_munis,insumoCode,variedad )

### Plots por departamento

In [21]:
def plot_map_departamentos(dtYear, dfGeoDATA, InsumoCode, variedad, Insumo_col='Codigo Insumo', variety_col='Unidad de Medida'):
    df_ventas = get_dfCode_variedad(dtYear, InsumoCode, variedad, Insumo_col, variety_col)

    # Normalizar clave de municipio en GeoJSON: eliminar TODOS los espacios, minúsculas y quitar acentos
    dfGeoDATA['muni_key'] = dfGeoDATA['NAME_1'].str.replace(' ', '').str.lower().apply(unidecode)  # Corregido: .str.replace
    
    # Normalizar municipios en ventas: eliminar TODOS los espacios, minúsculas y quitar acentos
    df_ventas['muni_key'] = df_ventas['Region Oferente'].str.replace(' ', '').str.lower().apply(unidecode)  # Corregido: .str.replace

    
    # Agrupar ventas por municipio (clave: muni_key)
    ventas_muni = df_ventas.groupby('muni_key')['Monto ofertado'].sum().reset_index()
    
    # Merge con GeoJSON
    gdf_merge = dfGeoDATA.merge(ventas_muni, on='muni_key', how='left')
    gdf_merge['monto_ofertado'] = gdf_merge['Monto ofertado'].fillna(0)

    # Plot
    fig = px.choropleth(
        gdf_merge,
        geojson=gdf_merge.geometry,
        locations=gdf_merge.index,
        color='monto_ofertado',
        hover_name="NAME_1",
        color_continuous_scale="Blues",
        title=f"Compras totales por municipio\n{variedad}",
        labels={'monto_ofertado': 'Monto total ofertado'}
    )
    fig.update_geos(fitbounds="locations", visible=False)
    fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})

    
    return fig.show()


In [30]:
#PATHS
current_folder = Path(os.getcwd())
soruce_folder="source_data"
filename_csv = "2023_all_results_all-MiniLM-L6-v2-similarity-es_score_value_0.7.csv"
filename_GeoJSON= "gadm41_GTM_1.json"

# Cargar la data por municipalidad
gdf_munis1 = gpd.read_file(current_folder/soruce_folder/filename_GeoJSON)
dfY=pd.read_csv(current_folder/ soruce_folder / filename_csv, sep=',',
                encoding='utf-8-sig',
                quoting=1, low_memory=False)
#codigo de insumo y varidad
insumoCode = 1821
Nvar=2
variety_dtYear=get_variedades(dfY,'Codigo Insumo','Unidad de Medida')
variedad = variety_dtYear[insumoCode][Nvar] #variedad

plot_map_departamentos(dfY,gdf_munis1,insumoCode,variedad )

### Ventas vs tiempo

In [34]:
#PATHS
current_folder = Path(os.getcwd())
soruce_folder="source_data"
filename_csv = "2023_all_results_all-MiniLM-L6-v2-similarity-es_score_value_0.7.csv"
filename_GeoJSON= "gadm41_GTM_1.json"

# Cargar la data por municipalidad
gdf_munis1 = gpd.read_file(current_folder/soruce_folder/filename_GeoJSON)
dfY=pd.read_csv(current_folder/ soruce_folder / filename_csv, sep=',',
                encoding='utf-8-sig',
                quoting=1, low_memory=False)
#codigo de insumo y varidad
insumoCode = 1821
Nvar=2
variety_dtYear=get_variedades(dfY,'Codigo Insumo','Unidad de Medida')
variedad = variety_dtYear[insumoCode][Nvar] #variedad
df_ventas_va = get_dfCode_variedad(dfY, insumoCode, variedad, 'Codigo Insumo', 'Unidad de Medida')

In [48]:
meses_va=df_ventas_va['Mes Publicacion'].unique()
precios_promedio=[] #precios promedio
stdv_precios_prom=[] #desviacion standard de cada precio
for k in range(len(meses_va)):
    df_mes_va=df_ventas_va[df_ventas_va['Mes Publicacion']==meses_va[k]]
    precio_unit_promedio_mes=df_mes_va['Precio unitario'].mean()
    stdv_unit_promedio_mes=df_mes_va['Precio unitario'].std()
    precios_promedio.append(float(precio_unit_promedio_mes))
    stdv_precios_prom.append(float(stdv_unit_promedio_mes))

In [49]:
print(precios_promedio)
print(stdv_precios_prom)

[11.40625, 11.60315789473684, 11.975000000000001, 11.275, 11.280769230769229, 11.725, 10.998275862068967, 9.9125, 10.883333333333333, 10.844999999999999]
[0.12938729237669142, 0.5258120981615955, 0.10606601717798238, 0.4636809247747852, 0.6892135986872173, 0.4406434688800762, 0.5740648853664867, 1.3268854509715597, 0.10408329997330641, 0.2192031021678301]


In [51]:
# Datos de ejemplo
meses_dic = {1:'Ene', 2:'Feb', 3:'Mar', 4:'Apr', 5:'May', 6:'Jun', 7:'Jul', 8:'Ago', 9:'Sep', 10:'Oct', 11:'Nov', 12:'Dic'}
meses=[]
for k in list(meses_va):
    meses.append(meses_dic[k])
desviaciones = stdv_precios_prom

# Crear el gráfico
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=meses,
    y=precios_promedio,
    mode='lines+markers',
    name='Precio Promedio',
    line=dict(color='blue', width=2),
    marker=dict(size=8),
    error_y=dict(
        type='data',  # tipo de error (en este caso, datos directos)
        array=desviaciones,  # valores de la desviación estándar
        visible=True,
        color='gray',
        thickness=1,
        width=3
    )
))

# Personalizar el layout
fig.update_layout(
    title='Evolución de Precios Mensuales con Desviación Estándar',
    xaxis_title='Mes',
    yaxis_title='Precio Promedio',
    showlegend=True,
    template='plotly_white'
)

fig.show()